In [1]:
import pandas as pd
pd.set_option('display.max_columns', 500)
pd.options.mode.chained_assignment = None  # default='warn'

import re
import string
import numpy as np
import matplotlib.pyplot as plt
from pandas_profiling import ProfileReport
import redditcleaner
from emoticon_fix import emoticon_fix
import emoji
import time as time
from collections import Counter

from unidecode import unidecode
import contractions

In [2]:
submission_cols = ['id', 'subreddit', 'created_utc', 'num_comments', 'score', 'link_flair_text', 'title', 'selftext']
comment_cols = ['author', 'parent_id', 'subreddit', 'created_utc', 'score', 'body']

# df = pd.read_csv('some_data.csv', usecols = ['col1','col2'], low_memory = True)

In [3]:
sep_sub = pd.read_csv('./datasets/sephora_sub_final.csv', usecols = submission_cols, low_memory=False)
print(sep_sub.shape)
sep_sub.tail()

(14847, 8)


created_utc      id  num_comments  score  \
14842   1646028704  t38otd             0      1   
14843   1646035026  t3adwq             0      1   
14844   1646051278  t3ehhv             0      1   
14845   1646053049  t3f0rk             0      1   
14846   1646053970  t3fbp2             0      1   

                                                selftext subreddit  \
14842  Any Sephora employees on here? I’ve been at Se...   Sephora   
14843  So, I took advantage of the 500 point deal thi...   Sephora   
14844                                                NaN   Sephora   
14845                                                NaN   Sephora   
14846    I am looking for something ideally clean beauty   Sephora   

                                                   title link_flair_text  
14842                                             Tatcha  Rant:downvote:  
14843                           I'm a Sephora idiot! LOL             PSA  
14844  Celebrity Eyebrow Artist and Anastasia Beverly...             PSA  
14845                                  huh, this is new!            Misc  
14846               SOS! Best AM eye Cream for puffiness          Advice

In [4]:
sep_cmt = pd.read_csv('./datasets/sephora_cmt_final.csv', usecols = comment_cols, low_memory=False)
print(sep_cmt.shape)
sep_cmt.head()

(196953, 6)


author                                               body  \
0        Anatomyofmeep  You have to spend 1000$ in a year to be approv...   
1        Anatomyofmeep  sorry you also get free In Store makeovers ( u...   
2          ashley125em             Thank u for letting me know about that   
3  complicationsoflife  It is worth it if you like getting your makeup...   
4              Nerys54  I usually order from Sephora in France but the...   

   created_utc  parent_id  score subreddit  
0   1436325997  t3_3ase55      1   Sephora  
1   1436326156  t3_3ase55      1   Sephora  
2   1444528805  t3_3gf2ep      1   Sephora  
3   1446607906  t3_3ase55      1   Sephora  
4   1447399683  t3_3smzui      1   Sephora

In [5]:
# mua = pd.read_csv('./datasets/makeupaddiction.csv', usecols = submission_cols, low_memory=False)

In [6]:
# ska = pd.read_csv('./datasets/skincareaddiction.csv', usecols = submission_cols, low_memory=False)

In [9]:
fra = pd.read_csv('./datasets/datasets_others/fragrance_post_sub_final.csv', usecols = submission_cols, low_memory = False)
print(fra.shape)
fra.head()

(39307, 8)


created_utc      id link_flair_text  num_comments  score  \
0   1585699643  fsokyr        Identify            41      4   
1   1585700525  fsotd0      Discussion             0      1   
2   1585702179  fsp9sc             NaN            16      1   
3   1585702951  fsph68    New to Group            19      7   
4   1585704868  fspzji             NaN            24      1   

                                            selftext  subreddit  \
0  I absolutely love mad men as a show. Everythin...  fragrance   
1  Was cleaning out my room because of quarantine...  fragrance   
2  I tried buying some samples, but the transacti...  fragrance   
3  I got samples from ELdO, Creed, Zoologist, and...  fragrance   
4    Which ones is the better hot weather fragrance?  fragrance   

                                               title  
0      What does Don Draper from Mad Men smell like?  
1  Just found a Dior Homme EDT sample from atleas...  
2  Anyone in the USA having issues ordering items...  
3  After making my way through a bunch of samples...  
4             Light Blue Intense or Aqva Atlantique?

In [10]:
# regex cleaner function defined
def regex(text):
    
    # text = text.lower() # Make lowercase. seems to mess up spacy
    # text = re.sub('[^A-Za-z0–9]',' ', text) # Remove special characters
   
    text = re.sub(r'\S*https?:\S*', ' ', text)   # removing the handful of spam urls or even legitimate urls.needs to be ' ', not ''
    text = re.sub(r'\[removed\]|\[deleted\]', ' ', text) # [removed] & [deleted] which are specific to reddit. needs to be ' ', not ''
    text = re.sub(r'\&amp;#x200B;|\&amp;|\’', '', text) # Remove frontslash. needs to be '', not ' '
    text = re.sub('/|-|_|:|\[|\]|\:|\(|\)|\{|\}','', text) # Remove frontslash. needs to be ' ', not ''
    
    return text

In [11]:
def clean_submissions(df,df_name):
    # df['created_utc'] 
    df['created_utc'] = df['created_utc'].apply(lambda x: time.strftime('%Y-%m-%d %H:%M:%S', time.localtime(x))).astype('datetime64[ns]')
  
    # df['title']
    df['title'] = df['title'].apply(lambda x:'' if x is (np.nan) else x)  
    
    # df['selftext']
    df['selftext'] = df['selftext'].apply(lambda x:'' if x is (np.nan) else x)
    
    # df['text']
    df['text'] = df['title']+' '+ df['selftext']
    
    
    # df['cleaned_text']
   
    df['cleaned_text'] = df['text'].apply(lambda x:regex(x)) #ok
    df['cleaned_text'] = df['cleaned_text'].map(redditcleaner.clean) #ok
    df['cleaned_text'] = df['cleaned_text'].apply(lambda x:emoticon_fix.emoticon_fix(x)) #ok   
    df['cleaned_text'] = df['cleaned_text'].apply(lambda x:emoji.demojize(x).replace('_', ' ')) #ok
    df['cleaned_text'] = df['cleaned_text'].apply(lambda x: unidecode(x))
    df['cleaned_text'] = df['cleaned_text'].apply(lambda x: contractions.fix(x))
    df['cleaned_text'] = df['cleaned_text'].apply(lambda x:x.translate(str.maketrans('', '',string.punctuation)))  #ok
    df['cleaned_text'] = df['cleaned_text'].apply(lambda x:' '.join(x.split()))
    df['cleaned_text'] = df['cleaned_text'].astype(str) 
    
    # 'word_count
    df['word_count_cleaned_text'] = df['cleaned_text'].apply(lambda x:len(x.split()))

    df = df[['id', 'subreddit', 'created_utc', 'num_comments', 'score', 'link_flair_text', 'title', 'selftext', 'text', 'cleaned_text','word_count_cleaned_text']]
    
    pd.DataFrame(df).to_csv(df_name, index=False)
    
    return df

In [12]:
def profile_clean_submissions(df, df_name, df_dropped, file_name, title):
    clean_submissions(df, df_name)
    df_dropped = pd.read_csv(file_name,low_memory=False)
    df_dropped = ProfileReport(df_dropped, title=title, explorative=True)
    return df_dropped

In [13]:
def clean_comments(df, df_name):
    # Dropping series
    df = df[df['author'] != 'AutoModerator']
    
    # df['new_parent_id']
    df['parent_id'] = df['parent_id'].str[3:] 
    
    # df['created_utc'] 
    df['created_utc'] = df['created_utc'].apply(lambda x: time.strftime('%Y-%m-%d %H:%M:%S', time.localtime(x))).astype('datetime64[ns]')
  
    # df['body']
    df['body'] = df['body'].apply(lambda x:'' if x is (np.nan) else x)
   
    # df['cleaned_body']
    df['cleaned_text'] = df['body'].apply(lambda x:regex(x)) #ok
    df['cleaned_text'] = df['cleaned_text'].map(redditcleaner.clean) #ok
    df['cleaned_text'] = df['cleaned_text'].apply(lambda x:emoticon_fix.emoticon_fix(x)) #ok   
    df['cleaned_text'] = df['cleaned_text'].apply(lambda x:emoji.demojize(x).replace('_', ' ')) #ok
    df['cleaned_text'] = df['cleaned_text'].apply(lambda x: unidecode(x))
    df['cleaned_text'] = df['cleaned_text'].apply(lambda x: contractions.fix(x))
    df['cleaned_text'] = df['cleaned_text'].apply(lambda x:x.translate(str.maketrans('', '',string.punctuation)))  #ok
    df['cleaned_text'] = df['cleaned_text'].apply(lambda x:' '.join(x.split()))
    df['cleaned_text'] = df['cleaned_text'].astype(str) 
    
    
    df['word_count_cleaned_text'] = df['cleaned_text'].apply(lambda x:len(x.split()))
      
    df = df[['author','parent_id', 'subreddit', 'created_utc', 'score', 'body', 'cleaned_text', 'word_count_cleaned_text']]
            
    pd.DataFrame(df).to_csv(df_name, index=False)
    
    return df

In [14]:
def clean_profile_comments(df, df_name, df_dropped, file_name, title):
    clean_comments(df, df_name)
    df_dropped = pd.read_csv(file_name,low_memory=False)
    df_dropped = ProfileReport(df_dropped, title=title, explorative=True)
    return df_dropped

## cleaning & profiling Sephora submission

In [15]:
# Sephora submissions
# fra, 'datasets/fra_dropped.csv', 'fra_dropped', './datasets/fra_dropped.csv', 'fragrance_dropped_Profiling')
profile_clean_submissions(sep_sub, 'datasets/sep_sub_final_dropped.csv', 'sep_sub_final_dropped', './datasets/sep_sub_final_dropped.csv', 'sephora_submissions_Profiling')

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [16]:
sep_sub_d = pd.read_csv('./datasets/sep_sub_final_dropped.csv', low_memory=False)
print(sep_sub_d.shape)
sep_sub_d.head()

(14847, 11)


id subreddit          created_utc  num_comments  score link_flair_text  \
0  24ck1c   Sephora  2014-04-30 14:24:44             0      1             NaN   
1  2paha7   Sephora  2014-12-15 04:53:51             1      1             NaN   
2  2qs93c   Sephora  2014-12-30 12:41:00             1      1             NaN   
3  34ws35   Sephora  2015-05-05 13:11:11             0      1             NaN   
4  3ase55   Sephora  2015-06-23 11:14:37             2      2             NaN   

                                               title selftext  \
0                has anyone ever used this lipstick?      NaN   
1  Are there any gift sets worth getting this hol...      NaN   
2  Sephora Free 2014 MAKE UP FOR EVER Birthday Se...      NaN   
3         In a Gift Box Reviews - Sephora Gift Cards      NaN   
4  Sephora VIB Rouge, Is it worth it? Do new VIB ...      NaN   

                                                text  \
0               has anyone ever used this lipstick?    
1  Are there any gift sets worth getting this hol...   
2  Sephora Free 2014 MAKE UP FOR EVER Birthday Se...   
3        In a Gift Box Reviews - Sephora Gift Cards    
4  Sephora VIB Rouge, Is it worth it? Do new VIB ...   

                                        cleaned_text  word_count_cleaned_text  
0                 has anyone ever used this lipstick                        6  
1  Are there any gift sets worth getting this hol...                       10  
2  Sephora Free 2014 MAKE UP FOR EVER Birthday Se...                       24  
3           In a Gift Box Reviews Sephora Gift Cards                        8  
4  Sephora VIB Rouge Is it worth it Do new VIB RO...                       19

In [17]:
sep_sub_d['cleaned_text'].isna().sum()

2

In [18]:
sep_sub_d = sep_sub_d.dropna(subset = ['cleaned_text'])
sep_sub_d.shape

(14845, 11)

In [19]:
pd.DataFrame(sep_sub_d).to_csv('datasets/sep_sub_final_cleaned.csv', index=False)

## cleaning & profiling sephora comments


In [20]:
# (sep_cmt, 'datasets/sep_cmt_dropped.csv', 'sep_cmt_dropped', './datasets/sep_cmt_dropped.csv', 'sep_cmt_dropped_Profiling')
# clean_profile_comments(df, df_name, df_dropped, file_name, title)
clean_profile_comments(sep_cmt,'datasets/sep_cmt_final_dropped.csv', 'sep_cmt_final_dropped', './datasets/sep_cmt_final_dropped.csv', 'sephora_cmt_dropped_Profiling')

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [21]:
sep_cmt_d = pd.read_csv('./datasets/sep_cmt_final_dropped.csv', low_memory=False)
sep_cmt_d.shape

(196953, 8)

In [22]:
duplicateRowsDF = sep_cmt_d[sep_cmt_d.duplicated()]
duplicateRowsDF.shape

(7, 8)

In [23]:
# pandas.DataFrame.duplicated(subset=None, keep= 'first')
sep_cmt_d.drop_duplicates(subset=None, keep= 'first', inplace=True)

In [24]:
sep_cmt_d.shape

(196946, 8)

In [25]:
sep_cmt_d['cleaned_text'].isna().sum()

2988

In [26]:
sep_cmt_d = sep_cmt_d.dropna(subset = ['cleaned_text'])

In [27]:
sep_cmt_d.shape

(193958, 8)

In [28]:
pd.DataFrame(sep_cmt_d).to_csv('datasets/sep_cmt_final_cleaned.csv', index=False)

## cleaning & profiling Fragrance submission


In [29]:
# fra, 'datasets/fra_dropped.csv', 'fra_dropped', './datasets/fra_dropped.csv', 'fragrance_dropped_Profiling')
profile_clean_submissions(fra, 'datasets/datasets_others/fra_final_dropped.csv', 'fra_final_dropped', './datasets/datasets_others/fra_final_dropped.csv', 'fragrance_dropped_Profiling')

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [30]:
fra_d = pd.read_csv('./datasets/datasets_others/fra_final_dropped.csv', low_memory=False)
fra_d.shape

(39307, 11)

In [31]:
duplicateRowsDF = fra_d[fra_d.duplicated()]
duplicateRowsDF.shape

(0, 11)

In [32]:
fra_d['cleaned_text'].isna().sum()

10

In [33]:
fra_d = fra_d.dropna(subset = ['cleaned_text'])
fra_d.shape

(39297, 11)

In [34]:
pd.DataFrame(fra_d).to_csv('datasets/datasets_others/fra_final_cleaned.csv', index=False)

#### the following cells are for checking if datasets are clear of duplcates and that 'clean_text' has no NaNs

In [ ]:
# duplicateRowsDF = df[df.duplicated()]
# duplicateRowsDF.shape

In [ ]:
# df['cleaned_text'].isna().sum()

In [ ]:
# df = df.dropna(subset = ['cleaned_text'])
# df.shape